# **Forelesning 4 - Språkmodellen Whisper**
I denne forelesningen skal vi se nærmere på bruk av Whisper modellen for bruk til tale-gjenkjenning, audio-til-tekst og noen kjekke anvendelser.

Vi kommer til å bruke en løsning av Whisper modellen, som krever lite kode. Da modellene er *pre-trained* og kan leses mer om på [Hugging face](https://huggingface.co/collections/openai/whisper-release-6501bba2cf999715fd953013).

## **Om Whisper-modellen**
Whisper er en banebrytende språkmodell utviklet av OpenAI, spesielt designet for å transkribere og oversette taledata til tekst. Modellen ble utgitt i september 2022 og er kjent for sine evner innen *automatisk talegjenkjenning* (ASR). Den har en åpen kildekode og støtter en rekke språk og dialekter, noe som gjør den svært allsidig for ulike bruksområder.

### **Nøkkelfunksjoner ved Whisper-modellen**
* *Flerspråklig*: Whisper er trent på et stort datasett som inneholder lyd fra flere språk, og kan derfor håndtere transkripsjon og oversettelse på tvers av mange ulike språk. F.eks. så har vi muligheten til å tolke norsk.

* *Fleksibilitet*: Modellen kan transkribere både taletil-tekst og oversette mellom språk samtidig. Dette gjør den nyttig for applikasjoner som tolkning, teksting, eller språklæring.

* *Robusthet*: Modellen er trent på store mengder mangfoldig data, inkludert bakgrunnsstøy, aksenter, og ustrukturert tale, noe som gir den evnen til å håndtere komplekse og uforutsigbare situasjoner.

* *Flere versjoner*: Whisper kommer i flere størrelser og kompleksitetsnivåer, fra små og raske modeller (som "tiny" og "base") til store og mer nøyaktige modeller (som "large"). Valget av modell avhenger av behovene dine, enten det handler om hastighet eller presisjon.

* *Bruksområder*: Whisper brukes i mange kontekster, som automatiserte transkripsjonssystemer, taleassistanter, og språklige grensesnitt. Den er også populær blant utviklere for å bygge applikasjoner som trenger pålitelig ASR-teknologi.

![Beskrivelse av Whisper](https://raw.githubusercontent.com/openai/whisper/main/approach.png)

# **Hva er tokens?**

* Èn **token** er et ord, eller en del av et ord, som brukes for å *bryte ned* naturlig språk til håndterbare *chunks*.
* Et eksempel kan være setningen "*Jeg liker å spise epler*", og den kan dele i flere tokens som f.eks. slik:
  * "Jeg"
  * "liker"
  * "å"
  * "spise"
  * "epler"
  * "."

Videre kan ord som "liker" bli delt opp igjen til ulike tokener som "lik" og "er". Legg merke til at at det kan være ord, deler av ord eller til og med symbol (som komma, punktum, spørsmåltegn... ).

Dette benytter Whisper modellen, når den skal prosessere audio-data (GPT bruker også denne metodikken). Dette øker effektiviteten, fordi modellen trenger ikke å lagre alle mulige ord i sitt *vokabular*, men kan *bygge sitt vokabular* på mindre enheter, altså disse tokenene.

### Chat GPT
Språkmodeller, ofte kalt LLM (Large Language Models) bruker tokens som grunnleggende enheter for å forstå og generere ny tekst. Når du skriver et setning til GPT (et såkalt *promt*), brytes dette ned til mindre enheter (kalt *tokens*), som modellen kan forstå.

### **Whisper**
Whsiper-modellen er en automatisk talegjenkjenningsmodell, og tar inn tale/lyd (som f.eks. .wav eller .mp3 fil). Første blir lyden konvertert til et spektrogram, som er en visuell representasjon av lydens frekvenser. Deretter blir denne informasjonen gjort om til tokens, altså som tekst.

Altså, sier du til Whisper-modellen "Jeg elsker cola.*", kan det bli "tokenisert" om til:
* "Jeg"
* "elsker"
* "cola"
* "."


# Vi starter med et enkelt eksempel

In [ ]:
# Her kan dere laste ned eksempeldata fra Nasjonalbiblioteket blant annet - Kongens tale.
!wget -N https://github.com/NbAiLab/nb-whisper/raw/main/audio/king.mp3
!wget -N https://github.com/NbAiLab/nb-whisper/raw/main/audio/erna.mp3
!wget -N https://github.com/NbAiLab/nb-whisper/raw/main/audio/knuthamsun.mp3

# Installer nødvendig bibliotek.
!pip install transformers #>=4.35.2

--2025-01-28 11:42:27--  https://github.com/NbAiLab/nb-whisper/raw/main/audio/king.mp3
Resolving github.com (github.com)... 140.82.114.3
Connecting to github.com (github.com)|140.82.114.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/NbAiLab/nb-whisper/main/audio/king.mp3 [following]
--2025-01-28 11:42:27--  https://raw.githubusercontent.com/NbAiLab/nb-whisper/main/audio/king.mp3
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1368336 (1.3M) [audio/mpeg]
Saving to: ‘king.mp3’

king.mp3            100%[===================>]   1.30M  --.-KB/s    in 0.07s   

Last-modified header missing -- time-stamps turned off.
2025-01-28 11:42:28 (20.0 MB/s) - ‘king.mp3’ saved [1368336/1368336]

--2025-01-28

In [ ]:
# Importer Audio biblioteket
from IPython.display import Audio

# Spill av MP3 filen for kongens tale
Audio("/content/king.mp3")

In [ ]:
Audio("/content/erna.mp3")

In [ ]:
# Nødvendige pakker som må installeres for å kjøre Whisper
!pip install transformers torch

# 1. Nasjonalbiblioteket's versjon av Whisper på norsk

In [ ]:
from transformers import pipeline

# Last modellen for å kunne gjøre automatisk tale-gjenkjenning (speech recognition) ved å bruke de ulike nb-whisper-models:

### Mulige modeller - a ulike str --> runtime, computational power etc. ###
# NbAiLabBeta/nb-whisper-tiny
# NbAiLabBeta/nb-whisper-base
# NbAiLabBeta/nb-whisper-small
# NbAiLabBeta/nb-whisper-medium
# NbAiLabBeta/nb-whisper-large

asr = pipeline("automatic-speech-recognition", "NbAiLabBeta/nb-whisper-medium")

# Transkriber
transcript = asr("king.mp3", generate_kwargs={'task': 'transcribe', 'language': 'no', 'return_timestamps': True})
transcript

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/4.50k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.06G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.80k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

...

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/339 [00:00<?, ?B/s]

Device set to use cpu
/usr/local/lib/python3.11/dist-packages/transformers/models/whisper/generation_whisper.py:512: FutureWarning: The input name `inputs` is deprecated. Please make sure to use `input_features` instead.
  warnings.warn(
You have passed task=transcribe, but also have set `forced_decoder_ids` to [[1, 50288], [2, 50359], [3, 50363]] which creates a conflict. `forced_decoder_ids` will be ignored in favor of task=transcribe.


{'text': ' Nordmenn er nordlendinger, trøndere, sørlendinger og folk fra alle andre regioner. Nordmenn er også innvandrere fra Afghanistan, Pakistan og Polen, Sverige, Somalia og Syria. Det er ikke alltid så lett å si hvor vi er fra, hvilken nasjonalitet vi tilhører. Det vi kaller hjem, er der hjertet vårt er. Og det kan ikke alltid plasseres innenfor landegrenser. Nordmenn er jenter som er glad i jenter, gutter som er glad i gutter, og jenter og gutter som er glad i hverandre. Nordmenn tror på Gud, Allah, altet og ingenting. Nordmenn liker Grieg, Hygo, Helbillies og Kari Bremnes. Med andre ord. Norge er dere. Norge er oss. Mitt største håp for Norge er at vi skal klare å ta vare på hverandre. At vi skal bygge dette landet videre på tillit, fellesskap og raushet.'}

Her viser vi bruk av Whisper-modellen i sin enkleste form, og her tar vi i bruk *whisper-small*. (Vi kunne brukt en av de større, men med Colab og forelesningens formål - holder vi det til *small*-versjonen).

## Vi kan også bruke OpenAI sin modell - som ikke er spesialisert for norsk

In [ ]:
# Vi kan også kjøre dette - men her er det ikke spesifisert at vi bruker Nasjonalbibliotekets versjon som
# er spesialisert for norsk.

asr_openai = pipeline("automatic-speech-recognition", model="openai/whisper-medium",
                      device=0)  # Ensures it runs on GPU if available

transcript_openai = asr_openai("king.mp3", generate_kwargs={"language": "no", "return_timestamps": True})
transcript_openai

config.json:   0%|          | 0.00/1.99k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.06G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.75k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/836k [00:00<?, ?B/s]

...

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/185k [00:00<?, ?B/s]

Device set to use cpu
/usr/local/lib/python3.11/dist-packages/transformers/models/whisper/generation_whisper.py:512: FutureWarning: The input name `inputs` is deprecated. Please make sure to use `input_features` instead.
  warnings.warn(
You have passed language=no, but also have set `forced_decoder_ids` to [[1, None], [2, 50359]] which creates a conflict. `forced_decoder_ids` will be ignored in favor of language=no.


{'text': ' Nordmen er nordlendinger, trøndere, sødlendinger og folk fra alle andre regioner. Nordmen er også innvandret fra Afghanistan, Pakistan og Polen, Sverige, Somalia og Syria. Det er ikke alltid så lett å si hvor vi er fra. Hvilken nasjonalitet vi tilhører. Det vi kaller hjem er der hjertet vårt er. Og det kan ikke alltid plasseres innenfor landegrensene. Når man er jenter som er glad i jenter, gutter som er glad i gutter, og som er glad i å være jenter, så er det ikke alltid så lett å si hvor vi er fra. Hvilken nasjonalitet vi tilhører. Det vi kaller hjem er der hjertet vårt er. Og det kan ikke alltid plasseres innenfor landegrensene. Når man er jenter som er glad i jenter, gutter som er glad i gutter, og som er glad i å være jenter, så er det ikke alltid så lett å si hvor vi er fra. gutter som er glad i gutter, og jenter og gutter som er glad i hverandre. Nordmenn tror på Gud, Allah, altet og ingenting. Nordmenn liker Grig, Hugo, Helbillies og Karibremnes. Med andre ord, Norge

### Sjekk om du har GPU aktivert
* Se oppe til høyre, og finn `Endre kjøringstype` og velg **GPU**.

In [ ]:
import torch

print("Torch using GPU:", torch.cuda.is_available())
print("Current device:", torch.cuda.current_device())
print("Device name:", torch.cuda.get_device_name(torch.cuda.current_device()))

# Arbeidsanbefaling
Hvis dere synes at denne modellen er interessant, så er det en veldig interessant artikkel dere bør lese fra OpenAI:


> Radford, A., Kim, J. W., Xu, T., Brockman, G., McLeavey, C., & Sutskever, I. (2022). Robust speech recognition via large-scale weak supervision. arXiv. https://doi.org/10.48550/arXiv.2212.04356

[Link til pdf](https://arxiv.org/pdf/2212.04356)

## Mer lesestoff
Ønsker dere å se på de norske modellene vi har brukt over, bør dere sjekke ut HuggingFace sidene til Nasjonalbiblioteket.

[Link til nettside](https://huggingface.co/NbAiLabBeta/nb-whisper-small)



# **Tilbake til Kongen's tale**

# 1.1 Det er mulighet for å modifisere bruk av Whisper modellen:

* Vi kan legge til *timestamps*, for *når* ting blir sagt i en mp3 fil.
* Dette gir oss muligheten til å finne ut når i en lang audio-fil sier noe interessant - kan være **veldig** tidsbesparende om du en gang skal transkribere masse data og lurer på når dere snakket om et eller annet tema.

In [ ]:
# chunk_length_s = bestemmer hvor lange "chunkene" er i sekunder.
asr('king.mp3', return_timestamps=True, chunk_length_s=28)

Whisper-modellen med `chunk_size_s=28` betyr at Whisper prosesserer data (mp3-filen) med 28-sekunders *chunks* - men gir ut outputtet i mer naturlige tale-segmenter.
Whisper tvinger altså ikke segmentene til å være nøyaktig 28 sekunder på grunn av sin naturlige setningsbaserte segmentering. I outputtet over, kan vi se at det er ganske naturlige setninger i hver `´timestamp´`.

#### **Prøv selv**
Prøv å kjør koden under:

```
transcript = asr("king.mp3", return_timestamps=True, chunk_length_s=30, stride_length_s=5)
```
Hvor:

* chunk_length_s=30: Øker vinduet for prosessering.
* stride_length_s=5: Legger til overlapp mellom *chunks* for å unngå å "miste" ord i kantene av chunks.


# 1.2 Vi kan gi timestamps for hvert enkelt ord
Dette kan være nyttig hvis man leter etter spesifikke ord i et intervju, podkast, film, etc...

In [ ]:
# Returnerer timestamps på ord-nivå
transcription = asr("king.mp3", chunk_length_s=28, return_timestamps="word", generate_kwargs={'task': 'transcribe', 'language': 'no'})
transcription

# Men hva hjelper det her?
Nå kan vi lage en funksjon i Python for å søke etter hvor et spesifikt ord blir brukt.

Potensiell use-case: Du ser gjennom $100$+ timer med opptak for transkripsjon og husker at i et intervju snakket du om noe ekstremt sjeldent og interessant, men kan ikke finne ut hvor det er. I stedet for å høre gjennom $10$+ timer og risikere å gå glipp av det, kan du bruke dette verktøyet. Mens koden kjører, kan du gjøre noe annet! :)

In [ ]:
def find_word_timestamps(transcription, word):
    """
    Funksjon som lager timestamps til spesifikke ord i transkripsjonen.

    Parametere:
    - transcription: Dictionary som inneholder transkripsjonsteksten og chuncks med timestamps.
    - word: Ordet man søker etter i transkripsjonen.

    Returns:
    - Liste av timestamps hvor det ordet ('word') befinner seg.
    """
    word = word.lower()  # Konverterer alt til lower-case for å forhindre case-sensitivity.
    timestamps = []

    for chunk in transcription['chunks']:
        # Ekstraher ord og fjern punctuation (punktum, komma etc.)
        chunk_text = chunk['text'].strip().lower().rstrip('.,')
        # Sjekker om chunken inneholder 'word' (ordet vi leter etter)
        if word in chunk_text.split():
            timestamps.append(chunk['timestamp'])

    return timestamps

# Eksempelbruk med asr function
# transcription = asr("path/to/audio/file")
word_to_find = "Bremnes" # Dette skal bare være et ord, ingen komma/kolon/semikolon etc.
timestamps = find_word_timestamps(transcription, word_to_find)

print(f"Timestamps for the word '{word_to_find}':", timestamps)

In [ ]:
# Test for andre ord
word_to_find = "Nordmenn" # Dette skal bare være et ord, ingen komma/kolon/semikolon etc.
timestamps = find_word_timestamps(transcription, word_to_find)

print(f"Timestamps for the word '{word_to_find}':", timestamps)

# 1.3 Transkribere fra ett språk til et annet språk.
Vi kan også transkribere til nynorsk eller engelsk, som vi viser nedenfor.

In [ ]:
# Transcribe to Nynorsk
asr("king.mp3", chunk_length_s=28, generate_kwargs={'task': 'transcribe', 'language': 'nn'})

In [ ]:
# Transcribe to English
asr("king.mp3", chunk_length_s=28, generate_kwargs={'task': 'transcribe', 'language': 'en'})

## 2. Bruk av OpenAI sin versjon av Whisper direkte
Her bruker vi altså ikke Nasjonalbibliotekets modell, men laster inn whisper for å kjøre det lokalt.

Men, da må man kjøre følgende

```
# Laster ned
!pip install openai-whisper

# Tar i bruk whisper biblioteket
import whisper
```

In [ ]:
!pip install openai-whisper

In [ ]:
import whisper

# Load Whisper model - her uten å spesifisere Nasjonalbiblioteket
model = whisper.load_model("medium")

# Transkriberer audio-filen
result = model.transcribe("/content/ML_Pod_transcript-kopi.wav", language='en') # språk kan være f.eks. 'en', 'no'

# Splitter transkriptet som setninger, for å gjøre det mer leselig.
text = result["text"]

# Definer avslutning av setninger for leseslighet
sentence_endings = '.!?'

# Add line breaks after each sentence-ending punctuation
formatted_text = ""
for char in text:
    formatted_text += char
    if char in sentence_endings:
        formatted_text += '\n'  # Add a newline after each sentence-ending punctuation

# Print ut transkriptet
print(formatted_text)

# Oppgaver

## Oppgave 1
Spill inn din egen stemme (bruk pc, mobil eller noe lignende), og last opp i Colab - og prøv å transkriber filen.

## Oppgave 2
List opp noen use-case'r for dette. Kanskje skal du gjøre et kvalitativ studie i masteroppgaven din, og må transkribere masse data?

## Oppgave 3
Lag en funksjon som transformerer en videofil (mp4) til audio-fil (som mp3 eller wav).

Da vil du få bruk for biblioteket `import ffmpeg`. Hva kan en slik funksjon brukes til?

___